#####Libraries
***

In [ ]:
import pandas as pd
import numpy as np
import seaborn as sns
import csv
from scipy.stats import norm
import statsmodels.api as sm
from patsy import dmatrices #a Python library for describing statistical models and building Design Matrices using R-like formulas.
import matplotlib.pyplot as plt
%matplotlib inline
from collections import Counter
from collections import defaultdict
!pip install yfinance --upgrade --no-cache-dir
import yfinance as yf
from pandas_datareader import data as pdr
yf.pdr_override()

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 62 kB 5.4 MB/s 
  Attempting uninstall: requests
    Found existing installation: requests 2.23.0
    Uninstalling requests-2.23.0:
      Successfully uninstalled requests-2.23.0


#####Load Dataset 
***

In [ ]:
#φτιάχνω τη λίστα με τα assets μου -> 50 μετοχές 
#διόρθωση : θα βγάλω τυχαία άλλες 4 μετοχές μαζί με την OGN επειδή δεν έχει το ίδιο μέγεθος με τις άλλες 
#βγάζω OGN ,WRK,HST,CE,ACN
assets= ["ABBV","AEP","AIZ","ALLE","AMAT","AMP","AMZN","AVB","AVY",   
  "AXP","BDX","BF-B","BMY","BR","CARR","CDW","CHTR","CNC",   
  "CNP","COP","CTAS","CZR","DG","DPZ","DRE","DXC","META","FTV",   
  "GOOG","GPC","HIG","JPM","KR","PG","PPL","PRU",   
  "PYPL","RE","ROL","ROST","UNH","URI","V","VRSK","XOM"]

In [ ]:
#άρα πρέπει να κατεβάσουμε όλα τα adj close για όλες τις τιμές όλων των μετοχών και να κάνουμε απόλυτο ranking και σε 5 κλασεις (targets)
r=pd.DataFrame(index=pdr.get_data_yahoo(assets[0],'2021-03-01','2022-06-01')['Adj Close'].index)

[*********************100%***********************]  1 of 1 completed


In [ ]:
#παίρνω τιμές για ένα χρόνο και 3 μήνες
for i in assets:
  # print('i metoxi me onoma:',i,'exei megethos',pdr.get_data_yahoo(i,'2021-01-01','2022-04-01')['Adj Close'].count())
  temp= pdr.get_data_yahoo(i,'2021-03-01','2022-06-01')['Adj Close']
  temp=temp.dropna()
  r[i]=temp.values

[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%********

In [ ]:
#φτιάχνω ένα αντίγραφο με τις τιμές για να το έχω 
rd=pd.DataFrame(r)
rd

ABBV         AEP         AIZ        ALLE        AMAT  \
Date                                                                     
2021-03-01  101.758369   72.935371  123.264771  109.629967  120.793564   
2021-03-02  101.232712   72.688156  123.596596  110.699768  116.100151   
2021-03-03  100.162674   72.564560  124.962952  110.071632  114.064697   
2021-03-04   99.167709   73.448792  125.001991  108.354057  106.950478   
2021-03-05  100.153282   75.017609  128.749710  111.210114  112.098404   
...                ...         ...         ...         ...         ...   
2022-05-24  147.728180  101.423317  179.328705  107.572716  106.058769   
2022-05-25  150.551773  101.681297  179.844635  107.662346  108.253166   
2022-05-26  149.174652  101.780518  178.634232  110.331497  114.776482   
2022-05-27  148.609924  102.762794  180.665848  113.080322  119.175240   
2022-05-31  146.004288  101.234802  175.965210  111.197975  116.990822   

                   AMP        AMZN         AVB         AVY         AXP  ...  \
Date                                                                    ...   
2021-03-01  223.396729  157.307007  169.428802  174.066818  136.349152  ...   
2021-03-02  220.188354  154.726501  170.577332  173.244690  136.879974  ...   
2021-03-03  218.140488  150.250000  173.620941  174.624695  140.163101  ...   
2021-03-04  211.850479  148.878494  170.414627  168.527222  140.251572  ...   
2021-03-05  216.784943  150.022995  170.031754  173.499176  144.822433  ...   
...                ...         ...         ...         ...         ...  ...   
2022-05-24  259.425537  104.099998  203.355850  161.470993  155.049759  ...   
2022-05-25  264.024170  106.775002  203.286423  163.969971  159.911545  ...   
2022-05-26  273.062195  111.077499  203.792297  167.440765  164.753433  ...   
2022-05-27  277.202972  115.146500  209.208252  172.161026  168.967667  ...   
2022-05-31  274.993225  120.209503  206.282059  171.862244  168.190582  ...   

                   PRU        PYPL          RE        ROL        ROST  \
Date                                                                    
2021-03-01   82.900154  273.630005  232.818268  33.455544  118.117958   
2021-03-02   83.274338  269.190002  232.127411  32.895824  115.247543   
2021-03-03   83.601761  255.059998  232.424881  31.874584  108.791573   
2021-03-04   82.853386  239.070007  229.978073  31.324680  109.741844   
2021-03-05   84.808487  239.050003  236.905838  32.345924  110.829262   
...                ...         ...         ...        ...         ...   
2022-05-24   99.719124   78.650002  272.294312  35.106831   77.048347   
2022-05-25  100.974388   80.120003  272.771454  35.226509   80.771210   
2022-05-26  103.346535   80.419998  277.532654  36.154049   86.360458   
2022-05-27  105.036690   85.209999  283.079163  36.513096   86.678146   
2022-05-31  105.016922   85.209999  280.802887  35.366138   84.404716   

                   UNH         URI           V        VRSK        XOM  
Date                                                                   
2021-03-01  326.841431  302.489990  214.501114  165.157486  52.391735  
2021-03-02  326.831726  293.420013  213.649551  164.504944  52.085182  
2021-03-03  325.103027  294.929993  212.738602  162.952637  52.503204  
2021-03-04  326.021118  288.600006  209.421509  159.828247  54.537560  
2021-03-05  339.000977  300.959991  213.293091  166.225327  56.599792  
...                ...         ...         ...         ...        ...  
2022-05-24  494.241119  267.739990  202.271744  170.328262  93.491615  
2022-05-25  494.767578  275.820007  203.479599  170.109055  95.373329  
2022-05-26  498.879974  284.839996  208.181274  173.088348  95.710060  
2022-05-27  503.727386  297.459991  212.503616  178.010666  96.650909  
2022-05-31  493.466309  298.179993  211.794876  174.294022  95.076218  

[317 rows x 45 columns]

In [ ]:
rd1= rd.pct_change().shift(-1)
rd1

ABBV       AEP       AIZ      ALLE      AMAT       AMP  \
Date                                                                     
2021-03-01 -0.005166 -0.003390  0.002692  0.009758 -0.038855 -0.014362   
2021-03-02 -0.010570 -0.001700  0.011055 -0.005674 -0.017532 -0.009301   
2021-03-03 -0.009933  0.012185  0.000312 -0.015604 -0.062370 -0.028835   
2021-03-04  0.009938  0.021359  0.029981  0.026359  0.048134  0.023292   
2021-03-05 -0.005529  0.020152  0.014251  0.028065 -0.068488  0.007962   
...              ...       ...       ...       ...       ...       ...   
2022-05-24  0.019113  0.002544  0.002877  0.000833  0.020690  0.017726   
2022-05-25 -0.009147  0.000976 -0.006730  0.024792  0.060260  0.034232   
2022-05-26 -0.003786  0.009651  0.011373  0.024914  0.038325  0.015164   
2022-05-27 -0.017533 -0.014869 -0.026018 -0.016646 -0.018329 -0.007972   
2022-05-31       NaN       NaN       NaN       NaN       NaN       NaN   

                AMZN       AVB       AVY       AXP  ...       PRU      PYPL  \
Date                                                ...                       
2021-03-01 -0.016404  0.006779 -0.004723  0.003893  ...  0.004514 -0.016226   
2021-03-02 -0.028932  0.017843  0.007966  0.023985  ...  0.003932 -0.052491   
2021-03-03 -0.009128 -0.018467 -0.034918  0.000631  ... -0.008952 -0.062691   
2021-03-04  0.007687 -0.002247  0.029502  0.032590  ...  0.023597 -0.000084   
2021-03-05 -0.016167  0.035238  0.032549  0.019955  ...  0.022722 -0.054215   
...              ...       ...       ...       ...  ...       ...       ...   
2022-05-24  0.025696 -0.000341  0.015476  0.031356  ...  0.012588  0.018690   
2022-05-25  0.040295  0.002488  0.021167  0.030279  ...  0.023493  0.003744   
2022-05-26  0.036632  0.026576  0.028191  0.025579  ...  0.016354  0.059562   
2022-05-27  0.043970 -0.013987 -0.001735 -0.004599  ... -0.000188  0.000000   
2022-05-31       NaN       NaN       NaN       NaN  ...       NaN       NaN   

                  RE       ROL      ROST       UNH       URI         V  \
Date                                                                     
2021-03-01 -0.002967 -0.016730 -0.024301 -0.000030 -0.029984 -0.003970   
2021-03-02  0.001281 -0.031045 -0.056018 -0.005289  0.005146 -0.004264   
2021-03-03 -0.010527 -0.017252  0.008735  0.002824 -0.021463 -0.015592   
2021-03-04  0.030124  0.032602  0.009909  0.039813  0.042827  0.018487   
2021-03-05  0.016768 -0.013661  0.063997  0.008845  0.005449  0.022562   
...              ...       ...       ...       ...       ...       ...   
2022-05-24  0.001752  0.003409  0.048319  0.001065  0.030179  0.005971   
2022-05-25  0.017455  0.026331  0.069199  0.008312  0.032702  0.023106   
2022-05-26  0.019985  0.009931  0.003679  0.009717  0.044306  0.020762   
2022-05-27 -0.008041 -0.031412 -0.026228 -0.020370  0.002420 -0.003335   
2022-05-31       NaN       NaN       NaN       NaN       NaN       NaN   

                VRSK       XOM  
Date                            
2021-03-01 -0.003951 -0.005851  
2021-03-02 -0.009436  0.008026  
2021-03-03 -0.019174  0.038747  
2021-03-04  0.040025  0.037813  
2021-03-05  0.020997 -0.000985  
...              ...       ...  
2022-05-24 -0.001287  0.020127  
2022-05-25  0.017514  0.003531  
2022-05-26  0.028438  0.009830  
2022-05-27 -0.020879 -0.016293  
2022-05-31       NaN       NaN  

[317 rows x 45 columns]

In [ ]:
#first: ranks assigned in order they appear in the array
rd2=rd1.rank(axis=1,method='first')
rd2=rd2.dropna()
rd2.astype(int)
jk=rd2.copy()
jk.astype(int)

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2021-03-01    25   30   39    45     1   12    10   42   26   40  ...   41   
2021-03-02    16   28   36    24    11   18     6   39   33   43  ...   31   
2021-03-03    24   40   32    19     2    6    25   16    5   33  ...   26   
2021-03-04     8   16   28    23    43   19     6    1   27   32  ...   20   
2021-03-05     9   34   28    41     1   22     7   43   42   33  ...   38   
...          ...  ...  ...   ...   ...  ...   ...  ...  ...  ...  ...  ...   
2022-05-23    32   44   39    19     6   15     4   25    9   10  ...   17   
2022-05-24    37   15   17    11    39   34    40    9   30   43  ...   25   
2022-05-25     2    4    3    28    41   37    38    6   23   33  ...   27   
2022-05-26     2    5   10    28    42   15    41   30   34   29  ...   20   
2022-05-27    13   16    6    14    11   22    45   17   35   30  ...   36   

            PYPL  RE  ROL  ROST  UNH  URI   V  VRSK  XOM  
Date                                                      
2021-03-01    11  33    9     4   37    3  28    29   21  
2021-03-02     2  30    4     1   25   32  27    17   34  
2021-03-03     1  23   17    37   34   11  20    12   45  
2021-03-04     3  29   33     7   37   41  13    39   34  
2021-03-05     2  29    8    45   24   19  37    35   13  
...          ...  ..  ...   ...  ...  ...  ..   ...  ...  
2022-05-23     5  27   21    12   37    8   7    22   30  
2022-05-24    36  14   19    44   12   41  22     7   38  
2022-05-25     8  19   30    42   12   36  25    20    7  
2022-05-26    45  22    8     3    6   44  23    36    7  
2022-05-27    37  21    3     5    9   39  33     8   15  

[316 rows x 45 columns]

In [ ]:
def rank_data(df1):
  for i in range(len(df1.index)):
    d=df1.loc[df1.index[i]]  #της κάθε μέρας d[1] δίνει μόνο τις τιμές 
    #print(d)
    d=d.sort_values()
    d[0:9]=1
    d[9:18]=2
    d[18:27]=3
    d[27:36]=4
    d[36:45]=5
    df1.loc[df1.index[i]]=d
    #print(df1.loc[df1.index[i]])
    #print(d)
  df1=df1.astype(int)
  return df1
r5=rd2.copy()
rd3=rank_data(r5)
rd3

ABBV  AEP  AIZ  ALLE  AMAT  AMP  AMZN  AVB  AVY  AXP  ...  PRU  \
Date                                                              ...        
2021-03-01     3    4    5     5     1    2     2    5    3    5  ...    5   
2021-03-02     2    4    4     3     2    2     1    5    4    5  ...    4   
2021-03-03     3    5    4     3     1    1     3    2    1    4  ...    3   
2021-03-04     1    2    4     3     5    3     1    1    3    4  ...    3   
2021-03-05     1    4    4     5     1    3     1    5    5    4  ...    5   
...          ...  ...  ...   ...   ...  ...   ...  ...  ...  ...  ...  ...   
2022-05-23     4    5    5     3     1    2     1    3    1    2  ...    2   
2022-05-24     5    2    2     2     5    4     5    1    4    5  ...    3   
2022-05-25     1    1    1     4     5    5     5    1    3    4  ...    3   
2022-05-26     1    1    2     4     5    2     5    4    4    4  ...    3   
2022-05-27     2    2    1     2     2    3     5    2    4    4  ...    4   

            PYPL  RE  ROL  ROST  UNH  URI  V  VRSK  XOM  
Date                                                     
2021-03-01     2   4    1     1    5    1  4     4    3  
2021-03-02     1   4    1     1    3    4  3     2    4  
2021-03-03     1   3    2     5    4    2  3     2    5  
2021-03-04     1   4    4     1    5    5  2     5    4  
2021-03-05     1   4    1     5    3    3  5     4    2  
...          ...  ..  ...   ...  ...  ... ..   ...  ...  
2022-05-23     1   3    3     2    5    1  1     3    4  
2022-05-24     4   2    3     5    2    5  3     1    5  
2022-05-25     1   3    4     5    2    4  3     3    1  
2022-05-26     5   3    1     1    1    5  3     4    1  
2022-05-27     5   3    1     1    1    5  4     1    2  

[316 rows x 45 columns]

#####Functions
***

In [ ]:
def RPS_calculation(hist_data, submission, asset_no=44):
    # print('check')
    if hist_data.shape[0]<=asset_no:
        return np.nan    
    # print('check')
    asset_id = pd.unique(hist_data.symbol)
    
    for i in range(len(pd.unique(hist_data.date))):
        if len(hist_data[hist_data.date == pd.unique(hist_data.date)[i]])<len(asset_id):
            for asset in [x for x in asset_id if x not in hist_data[hist_data.date == pd.unique(hist_data.date)[i]].symbol.values]:
                right_price = hist_data[hist_data.symbol==asset].sort_values(by='date')
                right_price = right_price[right_price.date <= pd.unique(hist_data.date)[i]]
                right_price = right_price.price.iloc[-1]
                hist_data = hist_data.append({'date' : pd.unique(hist_data.date)[i],
                                               'symbol' : asset,
                                               'price' : right_price}, ignore_index=True)

    #Compute percentage returns
    asset_id = sorted(asset_id) 

    #Compute percentage returns
    returns = pd.DataFrame(columns = ["ID", "Return"])
    
    min_date = min(hist_data.date)
    max_date = max(hist_data.date)
    # max_date = np.max(hist_data.date)
    
    for i in range(0,len(asset_id)):
        temp = hist_data.loc[hist_data.symbol==asset_id[i]]
        
        open_price = float(temp.loc[temp.date==min_date].price)
        close_price = float(temp.loc[temp.date==max_date].price)
        
        returns = returns.append({'ID': temp.symbol.iloc[0], 
                                'Return': (close_price - open_price)/open_price}, ignore_index=True)

    #Define the relevant position of each asset
    ranking = pd.DataFrame(columns=["ID", "Position", "Return"])
    ranking.ID = list(asset_id)
    ranking.Return = returns.Return
    ranking.Position = ranking.Return.rank(method = 'min')

    #Handle Ties
    Series_per_position = pd.DataFrame(columns=["Position","Series", "Rank", "Rank1", "Rank2","Rank3", "Rank4", "Rank5"])
    Series_per_position.Position = list(pd.unique(ranking.Position.sort_values(ascending=True)))
    temp = ranking.Position.value_counts()
    temp = pd.DataFrame(zip(temp.index, temp), columns = ["Rank", "Occurencies"])
    temp = temp.sort_values(by = ["Rank"],ascending=True)
    Series_per_position.Series = list(temp.Occurencies)
    Series_per_position

    total_ranks = Series_per_position.Position.values[-1]
    for i in range(0,Series_per_position.shape[0]):
    
        start_p = Series_per_position.Position[i]
        end_p = Series_per_position.Position[i] + Series_per_position.Series[i]
        temp = pd.DataFrame(columns = ["Position","Rank", "Rank1", "Rank2", "Rank3", "Rank4","Rank5"])
        temp.Position = list(range(int(start_p),int(end_p)))

        if(temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))].assign(Rank=1)
            temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(1,int(0.2*total_ranks+1))))].assign(Rank1=1.0)

        elif(temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))].assign(Rank=2)
            temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.2*total_ranks+1),int(0.4*total_ranks+1))))].assign(Rank2=1.0)

        elif(temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))].assign(Rank=3)
            temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.4*total_ranks+1),int(0.6*total_ranks+1))))].assign(Rank3=1.0)

        elif(temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))].assign(Rank=4)
            temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.6*total_ranks+1),int(0.8*total_ranks+1))))].assign(Rank4=1.0)

        elif(temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))].empty==False):
            temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))].assign(Rank=5)
            temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))] = temp.loc[temp.Position.isin(list(range(int(0.8*total_ranks+1),int(total_ranks+1))))].assign(Rank5=1.0)
        temp = temp.fillna(0)
        Series_per_position.iloc[i,2:Series_per_position.shape[1]] = temp.mean(axis = 0).iloc[1:temp.shape[1]]

    Series_per_position = Series_per_position.drop('Series', axis = 1)
    ranking = pd.merge(ranking,Series_per_position, on = "Position")
    ranking = ranking[["ID", "Return", "Position", "Rank", "Rank1", "Rank2", "Rank3", "Rank4", "Rank5"]]
    ranking = ranking.sort_values(["Position"])
    print(ranking)
    #Evaluate submission
    rps_sub = []
    #for aid in list((pd.unique(ranking.ID))):
    for aid in asset_id:

        target = np.cumsum(ranking.loc[ranking.ID==aid].iloc[:,4:9].values).tolist()
        frc = np.cumsum(submission.loc[submission.ID==aid].iloc[:,1:6].values).tolist()
        rps_sub.append(np.mean([(a - b)**2 for a, b in zip(target, frc)]))
    submission["RPS"] = rps_sub
    
    output = {'RPS' : np.mean(rps_sub),
              'details' : submission}
    
    return(output)

In [ ]:
#Αυτή η συνάρτηση παίρνει τα data και κάνει τη dummy μέτρηση για το διάστημα ενός χρόνου (όσο οριστεί στην ουσία το insample) για μια μετοχή
n=dict() 
def dummy(st,i,p):
  flag=False
  insample=st.iloc[p:-i]
  print('arxi',insample.head(1),'kai telos ',insample.tail(1),'mikos',len(insample))
  if(len(insample)!=253):
    print('---------------------------------------------------------------',flag)
  count=defaultdict(int)
  for word in insample.values:
    count[word]+=1
  print(word,count)
  count=sorted(count.items()) #list Η πρώτη τιμή είναι η κλάση και η δεύτερη πόσες φορές είδα τον αριθμό.
  temp=[]
  for k in range(5):
    flag=True
    for l in count:
      if(l[0]==k+1):
        temp.append(l[1]/len(insample))
        flag=False
        break
    if(flag):
      temp.append(0)
  # print(temp,count)
  data={
      'prediction':temp
  }
  forecast=pd.DataFrame(data)
  return forecast
# #για όλες τις μετοχές υπολογίζεται το counter τους
dummy(rd3['ABBV'],60,248)


arxi Date
2022-02-22    5
Name: ABBV, dtype: int64 kai telos  Date
2022-03-03    3
Name: ABBV, dtype: int64 mikos 8
--------------------------------------------------------------- False
3 defaultdict(<class 'int'>, {5: 1, 1: 1, 3: 2, 2: 2, 4: 2})


prediction
0       0.125
1       0.250
2       0.250
3       0.250
4       0.125

In [ ]:
def pred(st,p):
  pred=dict()
  for j in st:
    temp=[]
    date=[]
    for i in range(59,1,-1):
      # print(i)
      date.append(rd3[j].iloc[-i:-i+1].index.date[0])
      print(date)
      temp.append(dummy(rd3[j],i,p+(60-i))['prediction'].values)
      # pred[rd3[j].name]=temp
    #for the last day 
    date.append(rd3[j].iloc[-1:].index.date[0])
    temp.append(dummy(rd3[j],1,p+59)['prediction'].values)
    pred[rd3[j].name]=temp
  # print(date)
  pred['date']=date
  pred_final=pd.DataFrame.from_dict(pred)
  # pred_final['Date']=date
  # pred_final.set_index('Date')
  # print(pred_final)
  return pred_final
# t=pred(rd3,p)

In [ ]:
def create_historical(prob):
  prob=prob.rename_axis("symbol", axis="columns")
  prob=prob.T
  prob['date']=prob.columns.date[0]
  prob.columns = ['price', 'date']
  prob=prob.reset_index()
  prob=prob[['symbol','date','price']]
  return prob

In [ ]:
def RPS_data(prob_final,rd):
  RPS=pd.DataFrame()

  # RPS=RPS.drop('date',axis=1)
  # print(RPS.index[2])
  for k in prob_final.index: #for everyday of a stock->index
    prob=pd.DataFrame()
    prob1=pd.DataFrame()
    predic=pd.DataFrame()
    if(prob_final['date'][k]!=prob_final['date'].tail(1).values): #if it's not for the last day 
      #for historical data of two days 
      prob=rd.loc[(rd.index.date==prob_final['date'][k])]
      prob1=rd.loc[ (rd.index.date==prob_final['date'][k+1])]
      prob=create_historical(prob)
      prob1=create_historical(prob1)
      hist_data=prob.append(prob1)
      predic=prob_final.loc[prob_final['date']==prob_final['date'][k]] #find predictions of this day
      predic=predic.drop('date',axis=1)
      # print(predic)
      data=pd.DataFrame(index=predic.columns)
      data=data.reset_index()
      # print(data)
      data[['Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']]=(0,0,0,0,0)
      for i in range(len(np.array_split(predic.values[0],46))-1):
        data.loc[i,['Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']]=np.array_split(predic.values[0],46)[i][0]
      data.columns = ['ID','Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']
      # print(data)

      #now we have data->predictions and hist_data->historical data so now we can call the RPS
      rps=RPS_calculation(hist_data = hist_data , submission = data)['details']
      # print(rps) ->rps for every stock for one day 
      # print(rps['RPS'])
      tmp=pd.DataFrame(rps['RPS'].values).T
      # print(tmp.T)
      RPS=RPS.append(tmp,ignore_index=True)
      # print(RPS[RPS.index==k])

      
    else:
      #for the last day
      prob=rd.loc[(rd.index.date==prob_final['date'][k])]
      prob1=rd.loc[ (rd.index.date==rd.index.date[-1])]
      prob=create_historical(prob)
      prob1=create_historical(prob1)
      hist_data=prob.append(prob1)
      # print(hist_data)
      predic=prob_final.loc[prob_final['date']==prob_final['date'][k]] #find predictions of this day
      predic=predic.drop('date',axis=1)
      # print(predic)
      data=pd.DataFrame(index=predic.columns)
      data=data.reset_index()
      # print(data)
      data[['Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']]=(0,0,0,0,0)
      for i in range(len(np.array_split(predic.values[0],46))-1):
        data.loc[i,['Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']]=np.array_split(predic.values[0],46)[i][0]
      data.columns = ['ID','Rank 1', 'Rank 2', 'Rank 3', 'Rank 4','Rank 5']
      # print(data)

      #now we have data->predictions and hist_data->historical data so now we can call the RPS
      rps=RPS_calculation(hist_data = hist_data , submission = data)['details']
      # print(rps) ->rps for every stock for one day 
      # print(rps['RPS'])
      tmp=pd.DataFrame(rps['RPS'].values).T
      # print(tmp.T)
      RPS=RPS.append(tmp,ignore_index=True)              
  return RPS

In [ ]:
def create_RPS(prob_final,RPS):
  d=prob_final['date']
  name=prob_final.columns[:-1]
  # print(np.split(name.values,len(name)))
  # print(d.values)
  RPS['date']=d.values
  RPS=RPS.set_index('date')
  RPS.columns=assets
  return RPS

#####5 days
***

In [ ]:
t_5d=pred(rd3,251)

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
Name: PPL, dtype: int64 mikos 5
--------------------------------------------------------------- False
5 defaultdict(<class 'int'>, {4: 2, 2: 1, 3: 1, 5: 1})
[datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18), datetime.date(2022, 3, 21), datetime.date(2022, 3, 22), datetime.date(2022, 3, 23), datetime.date(2022, 3, 24), datetime.date(2022, 3, 25), datetime.date(2022, 3, 28), datetime.date(2022, 3, 29), datetime.date(2022, 3, 30), datetime.date(2022, 3, 31), datetime.date(2022, 4, 1), datetime.date(2022, 4, 4), datetime.date(2022, 4, 5), datetime.date(2022, 4, 6), datetime.date(2022, 4, 7)]
arxi Date
2022-03-31    4
Name: PPL, dtype: int64 kai telos  Date
2022-04-06    1
Name: PPL, dtype: int64 mikos 5
---------

In [ ]:
t_5d=pd.DataFrame.from_dict(t_5d)
t_5d.set_index('date')

ABBV                        AEP  \
date                                                               
2022-03-07  [0.0, 0.2, 0.2, 0.6, 0.0]  [0.0, 0.2, 0.0, 0.2, 0.6]   
2022-03-08  [0.0, 0.4, 0.2, 0.4, 0.0]  [0.0, 0.4, 0.0, 0.0, 0.6]   
2022-03-09  [0.0, 0.4, 0.2, 0.4, 0.0]  [0.2, 0.2, 0.0, 0.0, 0.6]   
2022-03-10  [0.0, 0.4, 0.2, 0.4, 0.0]  [0.2, 0.2, 0.0, 0.2, 0.4]   
2022-03-11  [0.0, 0.4, 0.0, 0.4, 0.2]  [0.2, 0.2, 0.0, 0.4, 0.2]   
2022-03-14  [0.0, 0.4, 0.0, 0.2, 0.4]  [0.2, 0.4, 0.0, 0.4, 0.0]   
2022-03-15  [0.0, 0.2, 0.0, 0.4, 0.4]  [0.2, 0.4, 0.0, 0.4, 0.0]   
2022-03-16  [0.0, 0.2, 0.0, 0.4, 0.4]  [0.2, 0.4, 0.0, 0.4, 0.0]   
2022-03-17  [0.0, 0.2, 0.0, 0.4, 0.4]  [0.4, 0.4, 0.0, 0.2, 0.0]   
2022-03-18  [0.0, 0.2, 0.2, 0.4, 0.2]  [0.6, 0.4, 0.0, 0.0, 0.0]   
2022-03-21  [0.0, 0.2, 0.2, 0.6, 0.0]  [0.6, 0.2, 0.0, 0.2, 0.0]   
2022-03-22  [0.0, 0.4, 0.2, 0.4, 0.0]  [0.6, 0.0, 0.2, 0.2, 0.0]   
2022-03-23  [0.0, 0.2, 0.4, 0.4, 0.0]  [0.4, 0.0, 0.2, 0.2, 0.2]   
2022-03-24  [0.0, 0.2, 0.6, 0.2, 0.0]  [0.2, 0.2, 0.2, 0.2, 0.2]   
2022-03-25  [0.0, 0.2, 0.6, 0.2, 0.0]  [0.0, 0.4, 0.2, 0.2, 0.2]   
2022-03-28  [0.0, 0.2, 0.8, 0.0, 0.0]  [0.0, 0.4, 0.4, 0.0, 0.2]   
2022-03-29  [0.2, 0.0, 0.8, 0.0, 0.0]  [0.0, 0.4, 0.4, 0.0, 0.2]   
2022-03-30  [0.2, 0.0, 0.6, 0.0, 0.2]  [0.0, 0.4, 0.4, 0.0, 0.2]   
2022-03-31  [0.2, 0.0, 0.4, 0.2, 0.2]  [0.0, 0.2, 0.4, 0.0, 0.4]   
2022-04-01  [0.2, 0.0, 0.4, 0.2, 0.2]  [0.0, 0.0, 0.4, 0.0, 0.6]   
2022-04-04  [0.2, 0.2, 0.2, 0.2, 0.2]  [0.0, 0.2, 0.2, 0.0, 0.6]   
2022-04-05  [0.0, 0.2, 0.2, 0.2, 0.4]  [0.0, 0.2, 0.0, 0.2, 0.6]   
2022-04-06  [0.0, 0.2, 0.2, 0.2, 0.4]  [0.0, 0.2, 0.0, 0.2, 0.6]   
2022-04-07  [0.0, 0.2, 0.2, 0.0, 0.6]  [0.2, 0.2, 0.0, 0.2, 0.4]   
2022-04-08  [0.0, 0.2, 0.0, 0.2, 0.6]  [0.2, 0.4, 0.0, 0.2, 0.2]   
2022-04-11  [0.2, 0.0, 0.0, 0.2, 0.6]  [0.2, 0.2, 0.2, 0.2, 0.2]   
2022-04-12  [0.4, 0.0, 0.0, 0.2, 0.4]  [0.2, 0.2, 0.2, 0.0, 0.4]   
2022-04-13  [0.6, 0.0, 0.0, 0.2, 0.2]  [0.4, 0.2, 0.2, 0.0, 0.2]   
2022-04-14  [0.6, 0.0, 0.0, 0.2, 0.2]  [0.2, 0.2, 0.2, 0.2, 0.2]   
2022-04-18  [0.8, 0.0, 0.0, 0.0, 0.2]  [0.2, 0.0, 0.4, 0.2, 0.2]   
2022-04-19  [0.8, 0.0, 0.0, 0.0, 0.2]  [0.2, 0.2, 0.2, 0.2, 0.2]   
2022-04-20  [0.8, 0.0, 0.0, 0.0, 0.2]  [0.2, 0.4, 0.2, 0.2, 0.0]   
2022-04-21  [0.6, 0.0, 0.0, 0.0, 0.4]  [0.0, 0.4, 0.2, 0.4, 0.0]   
2022-04-22  [0.6, 0.0, 0.0, 0.2, 0.2]  [0.0, 0.4, 0.2, 0.2, 0.2]   
2022-04-25  [0.4, 0.0, 0.0, 0.4, 0.2]  [0.0, 0.4, 0.2, 0.2, 0.2]   
2022-04-26  [0.2, 0.0, 0.0, 0.4, 0.4]  [0.0, 0.2, 0.2, 0.4, 0.2]   
2022-04-27  [0.0, 0.0, 0.0, 0.6, 0.4]  [0.0, 0.0, 0.4, 0.4, 0.2]   
2022-04-28  [0.2, 0.0, 0.0, 0.6, 0.2]  [0.0, 0.0, 0.4, 0.4, 0.2]   
2022-04-29  [0.4, 0.0, 0.0, 0.4, 0.2]  [0.0, 0.2, 0.4, 0.4, 0.0]   
2022-05-02  [0.4, 0.0, 0.0, 0.4, 0.2]  [0.0, 0.4, 0.2, 0.4, 0.0]   
2022-05-03  [0.4, 0.0, 0.0, 0.6, 0.0]  [0.0, 0.4, 0.4, 0.2, 0.0]   
2022-05-04  [0.6, 0.0, 0.0, 0.4, 0.0]  [0.0, 0.6, 0.2, 0.2, 0.0]   
2022-05-05  [0.4, 0.0, 0.0, 0.4, 0.2]  [0.0, 0.6, 0.2, 0.2, 0.0]   
2022-05-06  [0.2, 0.0, 0.0, 0.6, 0.2]  [0.0, 0.4, 0.2, 0.4, 0.0]   
2022-05-09  [0.2, 0.0, 0.0, 0.6, 0.2]  [0.0, 0.2, 0.2, 0.4, 0.2]   
2022-05-10  [0.2, 0.0, 0.0, 0.6, 0.2]  [0.0, 0.4, 0.0, 0.4, 0.2]   
2022-05-11  [0.0, 0.0, 0.0, 0.8, 0.2]  [0.0, 0.2, 0.0, 0.4, 0.4]   
2022-05-12  [0.0, 0.0, 0.0, 0.8, 0.2]  [0.2, 0.2, 0.0, 0.2, 0.4]   
2022-05-13  [0.2, 0.0, 0.0, 0.6, 0.2]  [0.2, 0.4, 0.0, 0.0, 0.4]   
2022-05-16  [0.2, 0.0, 0.0, 0.4, 0.4]  [0.2, 0.4, 0.2, 0.0, 0.2]   
2022-05-17  [0.4, 0.0, 0.0, 0.2, 0.4]  [0.2, 0.4, 0.2, 0.0, 0.2]   
2022-05-18  [0.4, 0.0, 0.0, 0.0, 0.6]  [0.2, 0.4, 0.2, 0.0, 0.2]   
2022-05-19  [0.4, 0.0, 0.2, 0.0, 0.4]  [0.0, 0.6, 0.2, 0.0, 0.2]   
2022-05-20  [0.2, 0.2, 0.2, 0.0, 0.4]  [0.0, 0.4, 0.2, 0.2, 0.2]   
2022-05-23  [0.4, 0.2, 0.2, 0.0, 0.2]  [0.2, 0.4, 0.0, 0.2, 0.2]   
2022-05-24  [0.2, 0.2, 0.2, 0.2, 0.2]  [0.2, 0.2, 0.0, 0.2, 0.4]   
2022-05-25  [0.2, 0.2, 0.2, 0.2, 0.2]  [0.2, 0.4, 0.0, 0.2, 0.2]   
2022-05-26  [0.4, 0.2

In [ ]:
RPS_5d= RPS_data(t_5d,rd)
RPS_5d= create_RPS(t_5d,RPS_5d)
RPS_5d
print(RPS_5d.mean(axis=1).mean())

      ID    Return  Position Rank Rank1 Rank2 Rank3 Rank4 Rank5
11  BF-B -0.054752       1.0  1.0   1.0   0.0   0.0   0.0   0.0
38   ROL -0.040931       2.0  1.0   1.0   0.0   0.0   0.0   0.0
33    PG -0.039584       3.0  1.0   1.0   0.0   0.0   0.0   0.0
10   BDX -0.039558       4.0  1.0   1.0   0.0   0.0   0.0   0.0
31    KR -0.036493       5.0  1.0   1.0   0.0   0.0   0.0   0.0
3   ALLE -0.028763       6.0  1.0   1.0   0.0   0.0   0.0   0.0
40   UNH -0.027543       7.0  1.0   1.0   0.0   0.0   0.0   0.0
26   FTV -0.025787       8.0  1.0   1.0   0.0   0.0   0.0   0.0
19   COP -0.024390       9.0  1.0   1.0   0.0   0.0   0.0   0.0
17   CNC -0.022997      10.0  2.0   0.0   1.0   0.0   0.0   0.0
22    DG -0.021893      11.0  2.0   0.0   1.0   0.0   0.0   0.0
1    AEP -0.020666      12.0  2.0   0.0   1.0   0.0   0.0   0.0
7    AVB -0.018930      13.0  2.0   0.0   1.0   0.0   0.0   0.0
23   DPZ -0.017297      14.0  2.0   0.0   1.0   0.0   0.0   0.0
24   DRE -0.015957      15.0  2.0   0.0 

In [ ]:
#for 1st April
print(RPS_5d.iloc[18].mean())
#for 29 April 
print(RPS_5d.iloc[37].mean())
#for 27 May
print(RPS_5d.iloc[57].mean())
RPS_5d.mean(axis=1)

0.15431111111111112
0.17386666666666667
0.18951111111111113


date
2022-03-07    0.279111
2022-03-08    0.222933
2022-03-09    0.168178
2022-03-10    0.185956
2022-03-11    0.180622
2022-03-14    0.188800
2022-03-15    0.171733
2022-03-16    0.168889
2022-03-17    0.146133
2022-03-18    0.253511
2022-03-21    0.155733
2022-03-22    0.221511
2022-03-23    0.178489
2022-03-24    0.163200
2022-03-25    0.256711
2022-03-28    0.185956
2022-03-29    0.187733
2022-03-30    0.181333
2022-03-31    0.154311
2022-04-01    0.212978
2022-04-04    0.166044
2022-04-05    0.132267
2022-04-06    0.169956
2022-04-07    0.166400
2022-04-08    0.220800
2022-04-11    0.155378
2022-04-12    0.236444
2022-04-13    0.152533
2022-04-14    0.164622
2022-04-18    0.208711
2022-04-19    0.183111
2022-04-20    0.211556
2022-04-21    0.191644
2022-04-22    0.206578
2022-04-25    0.153244
2022-04-26    0.185956
2022-04-27    0.209067
2022-04-28    0.173867
2022-04-29    0.190933
2022-05-02    0.160000
2022-05-03    0.149689
2022-05-04    0.217956
2022-05-05    0.150400
2022-0

#####10 days
***

In [ ]:
t_10d=pred(rd3,246)
t_10d=pd.DataFrame.from_dict(t_10d)
t_10d.set_index('date')
RPS_10d= RPS_data(t_10d,rd)
RPS_10d= create_RPS(t_10d,RPS_10d)
RPS_10d
print(RPS_10d.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
--------------------------------------------------------------- False
4 defaultdict(<class 'int'>, {5: 2, 3: 3, 1: 2, 2: 1, 4: 2})
[datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18)]
arxi Date
2022-03-04    3
Name: UNH, dtype: int64 kai telos  Date
2022-03-17    1
Name: UNH, dtype: int64 mikos 10
--------------------------------------------------------------- False
1 defaultdict(<class 'int'>, {3: 3, 1: 3, 5: 1, 2: 1, 4: 2})
[datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18), datetime.dat

In [ ]:
#for 1st April
print(RPS_10d.iloc[18].mean())
#for 29 April 
print(RPS_10d.iloc[37].mean())
#for 27 May
print(RPS_10d.iloc[57].mean())
RPS_10d.mean(axis=1)

0.15662222222222225
0.1600888888888889
0.1806222222222222


date
2022-03-07    0.235467
2022-03-08    0.211556
2022-03-09    0.150400
2022-03-10    0.176444
2022-03-11    0.179111
2022-03-14    0.193867
2022-03-15    0.184089
2022-03-16    0.158222
2022-03-17    0.156178
2022-03-18    0.191822
2022-03-21    0.145867
2022-03-22    0.208089
2022-03-23    0.157333
2022-03-24    0.163111
2022-03-25    0.185689
2022-03-28    0.171911
2022-03-29    0.189067
2022-03-30    0.174044
2022-03-31    0.156622
2022-04-01    0.211822
2022-04-04    0.155200
2022-04-05    0.143644
2022-04-06    0.168444
2022-04-07    0.164533
2022-04-08    0.190933
2022-04-11    0.146400
2022-04-12    0.217244
2022-04-13    0.136800
2022-04-14    0.179467
2022-04-18    0.206578
2022-04-19    0.148711
2022-04-20    0.169511
2022-04-21    0.180178
2022-04-22    0.205600
2022-04-25    0.140444
2022-04-26    0.169244
2022-04-27    0.174489
2022-04-28    0.160089
2022-04-29    0.185600
2022-05-02    0.170578
2022-05-03    0.172711
2022-05-04    0.163911
2022-05-05    0.145422
2022-0

#####15 days
***

In [ ]:
t_15d=pred(rd3,241)
t_15d=pd.DataFrame.from_dict(t_15d)
t_15d.set_index('date')
RPS_15d= RPS_data(t_15d,rd)
RPS_15d= create_RPS(t_15d,RPS_15d)
RPS_15d
print(RPS_15d.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
--------------------------------------------------------------- False
4 defaultdict(<class 'int'>, {5: 4, 4: 4, 3: 4, 1: 2, 2: 1})
[datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18)]
arxi Date
2022-02-25    4
Name: UNH, dtype: int64 kai telos  Date
2022-03-17    1
Name: UNH, dtype: int64 mikos 15
--------------------------------------------------------------- False
1 defaultdict(<class 'int'>, {4: 4, 5: 3, 3: 4, 1: 3, 2: 1})
[datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18), datetime.dat

In [ ]:
#for 1st April
print(RPS_15d.iloc[18].mean())
#for 29 April 
print(RPS_15d.iloc[37].mean())
#for 27 May
print(RPS_15d.iloc[57].mean())
RPS_15d.mean(axis=1)

0.17046913580246917
0.15063703703703704
0.18046419753086418


date
2022-03-07    0.211793
2022-03-08    0.197412
2022-03-09    0.146884
2022-03-10    0.167190
2022-03-11    0.167032
2022-03-14    0.189274
2022-03-15    0.192474
2022-03-16    0.148622
2022-03-17    0.177462
2022-03-18    0.162489
2022-03-21    0.169837
2022-03-22    0.171733
2022-03-23    0.161501
2022-03-24    0.154667
2022-03-25    0.186943
2022-03-28    0.168494
2022-03-29    0.181412
2022-03-30    0.175881
2022-03-31    0.170469
2022-04-01    0.172958
2022-04-04    0.167585
2022-04-05    0.163240
2022-04-06    0.164543
2022-04-07    0.162844
2022-04-08    0.176395
2022-04-11    0.147398
2022-04-12    0.200770
2022-04-13    0.146054
2022-04-14    0.182202
2022-04-18    0.194844
2022-04-19    0.149728
2022-04-20    0.151190
2022-04-21    0.156405
2022-04-22    0.196425
2022-04-25    0.126064
2022-04-26    0.168138
2022-04-27    0.183467
2022-04-28    0.150637
2022-04-29    0.189788
2022-05-02    0.162528
2022-05-03    0.164543
2022-05-04    0.167111
2022-05-05    0.145936
2022-0

#####One Month (22 working days)
***

In [ ]:
t_1m=pred(rd3,234)
t_1m=pd.DataFrame.from_dict(t_1m)
t_1m.set_index('date')
RPS_1m= RPS_data(t_1m,rd)
RPS_1m= create_RPS(t_1m,RPS_1m)
RPS_1m
print(RPS_1m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
--------------------------------------------------------------- False
4 defaultdict(<class 'int'>, {2: 4, 4: 5, 3: 6, 5: 5, 1: 2})
[datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18)]
arxi Date
2022-02-15    4
Name: UNH, dtype: int64 kai telos  Date
2022-03-17    1
Name: UNH, dtype: int64 mikos 22
--------------------------------------------------------------- False
1 defaultdict(<class 'int'>, {4: 5, 2: 3, 3: 6, 5: 5, 1: 3})
[datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18), datetime.dat

In [ ]:
#for 1st April
print(RPS_1m.iloc[18].mean())
#for 29 April 
print(RPS_1m.iloc[37].mean())
#for 27 May
print(RPS_1m.iloc[57].mean())
RPS_1m.mean(axis=1)

0.1618732782369146
0.15482093663911844
0.18253443526170798


date
2022-03-07    0.196878
2022-03-08    0.183893
2022-03-09    0.143581
2022-03-10    0.158457
2022-03-11    0.161102
2022-03-14    0.182571
2022-03-15    0.189954
2022-03-16    0.154674
2022-03-17    0.178457
2022-03-18    0.153646
2022-03-21    0.171442
2022-03-22    0.156621
2022-03-23    0.162534
2022-03-24    0.155868
2022-03-25    0.177098
2022-03-28    0.180496
2022-03-29    0.155556
2022-03-30    0.168246
2022-03-31    0.161873
2022-04-01    0.180496
2022-04-04    0.155427
2022-04-05    0.164279
2022-04-06    0.173792
2022-04-07    0.159908
2022-04-08    0.175592
2022-04-11    0.155243
2022-04-12    0.178825
2022-04-13    0.150119
2022-04-14    0.161359
2022-04-18    0.190560
2022-04-19    0.155445
2022-04-20    0.153444
2022-04-21    0.153994
2022-04-22    0.189201
2022-04-25    0.129550
2022-04-26    0.162222
2022-04-27    0.178163
2022-04-28    0.154821
2022-04-29    0.194417
2022-05-02    0.159816
2022-05-03    0.171038
2022-05-04    0.146703
2022-05-05    0.138274
2022-0

#####Two Months(44 working days)
***

In [ ]:
t_2m=pred(rd3,212)
t_2m=pd.DataFrame.from_dict(t_2m)
t_2m.set_index('date')
RPS_2m= RPS_data(t_2m,rd)
RPS_2m= create_RPS(t_2m,RPS_2m)
RPS_2m
print(RPS_2m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
--------------------------------------------------------------- False
4 defaultdict(<class 'int'>, {2: 9, 4: 11, 3: 13, 5: 8, 1: 3})
[datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18)]
arxi Date
2022-01-13    4
Name: UNH, dtype: int64 kai telos  Date
2022-03-17    1
Name: UNH, dtype: int64 mikos 44
--------------------------------------------------------------- False
1 defaultdict(<class 'int'>, {4: 11, 3: 13, 5: 8, 2: 8, 1: 4})
[datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18), datetime

In [ ]:
#for 1st April
print(RPS_2m.iloc[18].mean())
#for 29 April 
print(RPS_2m.iloc[37].mean())
#for 27 May
print(RPS_2m.iloc[57].mean())
RPS_2m.mean(axis=1)

0.1653305785123967
0.15603305785123966
0.17912764003673093


date
2022-03-07    0.176198
2022-03-08    0.178903
2022-03-09    0.144982
2022-03-10    0.153875
2022-03-11    0.158949
2022-03-14    0.175124
2022-03-15    0.176143
2022-03-16    0.157484
2022-03-17    0.177920
2022-03-18    0.151483
2022-03-21    0.162635
2022-03-22    0.155638
2022-03-23    0.157966
2022-03-24    0.156800
2022-03-25    0.181938
2022-03-28    0.179027
2022-03-29    0.151625
2022-03-30    0.159858
2022-03-31    0.165331
2022-04-01    0.173535
2022-04-04    0.151717
2022-04-05    0.146644
2022-04-06    0.156630
2022-04-07    0.151713
2022-04-08    0.168186
2022-04-11    0.150165
2022-04-12    0.171387
2022-04-13    0.141024
2022-04-14    0.163586
2022-04-18    0.180073
2022-04-19    0.158563
2022-04-20    0.156001
2022-04-21    0.153962
2022-04-22    0.171823
2022-04-25    0.142112
2022-04-26    0.156616
2022-04-27    0.163251
2022-04-28    0.156033
2022-04-29    0.176455
2022-05-02    0.155927
2022-05-03    0.166612
2022-05-04    0.149522
2022-05-05    0.148714
2022-0

#####Three months(66 working days)
***

In [ ]:
t_3m=pred(rd3,190)
t_3m=pd.DataFrame.from_dict(t_3m)
t_3m.set_index('date')
RPS_3m= RPS_data(t_3m,rd)
RPS_3m= create_RPS(t_3m,RPS_3m)
RPS_3m
print(RPS_3m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
--------------------------------------------------------------- False
4 defaultdict(<class 'int'>, {4: 17, 5: 12, 2: 14, 3: 18, 1: 5})
[datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18)]
arxi Date
2021-12-13    4
Name: UNH, dtype: int64 kai telos  Date
2022-03-17    1
Name: UNH, dtype: int64 mikos 66
--------------------------------------------------------------- False
1 defaultdict(<class 'int'>, {4: 16, 5: 12, 2: 14, 3: 18, 1: 6})
[datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18), date

In [ ]:
#for 1st April
print(RPS_3m.iloc[18].mean())
#for 29 April 
print(RPS_3m.iloc[37].mean())
#for 27 May
print(RPS_3m.iloc[57].mean())
RPS_3m.mean(axis=1)

0.15875931027446183
0.15443526170798896
0.17018467503315987


date
2022-03-07    0.173984
2022-03-08    0.172199
2022-03-09    0.147195
2022-03-10    0.153354
2022-03-11    0.156631
2022-03-14    0.172482
2022-03-15    0.178163
2022-03-16    0.157678
2022-03-17    0.175853
2022-03-18    0.151242
2022-03-21    0.164016
2022-03-22    0.151662
2022-03-23    0.159310
2022-03-24    0.150046
2022-03-25    0.182890
2022-03-28    0.176535
2022-03-29    0.143849
2022-03-30    0.156172
2022-03-31    0.158759
2022-04-01    0.178478
2022-04-04    0.149481
2022-04-05    0.149752
2022-04-06    0.155415
2022-04-07    0.146046
2022-04-08    0.168385
2022-04-11    0.153368
2022-04-12    0.166783
2022-04-13    0.141286
2022-04-14    0.160278
2022-04-18    0.181202
2022-04-19    0.159065
2022-04-20    0.156425
2022-04-21    0.155831
2022-04-22    0.168271
2022-04-25    0.146867
2022-04-26    0.153903
2022-04-27    0.160928
2022-04-28    0.154435
2022-04-29    0.170650
2022-05-02    0.154623
2022-05-03    0.165334
2022-05-04    0.146918
2022-05-05    0.145330
2022-0

#####Six months (132 working days)
***

In [ ]:
t_6m=pred(rd3,124)
t_6m=pd.DataFrame.from_dict(t_6m)
t_6m.set_index('date')
RPS_6m= RPS_data(t_6m,rd)
RPS_6m= create_RPS(t_6m,RPS_6m)
RPS_6m
print(RPS_6m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
--------------------------------------------------------------- False
4 defaultdict(<class 'int'>, {3: 35, 1: 14, 5: 30, 4: 28, 2: 25})
[datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18)]
arxi Date
2021-09-09    1
Name: UNH, dtype: int64 kai telos  Date
2022-03-17    1
Name: UNH, dtype: int64 mikos 132
--------------------------------------------------------------- False
1 defaultdict(<class 'int'>, {1: 15, 5: 30, 4: 28, 3: 34, 2: 25})
[datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18), d

In [ ]:
#for 1st April
print(RPS_6m.iloc[18].mean())
#for 29 April 
print(RPS_6m.iloc[37].mean())
#for 27 May
print(RPS_6m.iloc[57].mean())
RPS_6m.mean(axis=1)

0.15928629731660038
0.15738598102234466
0.17146413631262117


date
2022-03-07    0.166436
2022-03-08    0.165989
2022-03-09    0.153293
2022-03-10    0.158503
2022-03-11    0.156664
2022-03-14    0.162906
2022-03-15    0.166274
2022-03-16    0.155693
2022-03-17    0.164872
2022-03-18    0.154280
2022-03-21    0.164261
2022-03-22    0.150362
2022-03-23    0.160702
2022-03-24    0.151618
2022-03-25    0.168896
2022-03-28    0.169189
2022-03-29    0.148270
2022-03-30    0.157719
2022-03-31    0.159286
2022-04-01    0.171134
2022-04-04    0.145727
2022-04-05    0.146173
2022-04-06    0.152480
2022-04-07    0.151737
2022-04-08    0.168448
2022-04-11    0.151785
2022-04-12    0.165476
2022-04-13    0.149163
2022-04-14    0.157711
2022-04-18    0.172154
2022-04-19    0.154284
2022-04-20    0.152463
2022-04-21    0.158533
2022-04-22    0.165842
2022-04-25    0.145458
2022-04-26    0.155622
2022-04-27    0.163100
2022-04-28    0.157386
2022-04-29    0.169554
2022-05-02    0.153290
2022-05-03    0.164451
2022-05-04    0.145358
2022-05-05    0.147033
2022-0

#####Ten months (220 working days)
***

In [ ]:
t_10m=pred(rd3,36)
t_10m=pd.DataFrame.from_dict(t_10m)
t_10m.set_index('date')
RPS_10m= RPS_data(t_10m,rd)
RPS_10m= create_RPS(t_10m,RPS_10m)
RPS_10m
print(RPS_10m.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
--------------------------------------------------------------- False
4 defaultdict(<class 'int'>, {3: 54, 5: 44, 2: 44, 4: 48, 1: 30})
[datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18)]
arxi Date
2021-05-05    3
Name: UNH, dtype: int64 kai telos  Date
2022-03-17    1
Name: UNH, dtype: int64 mikos 220
--------------------------------------------------------------- False
1 defaultdict(<class 'int'>, {3: 53, 5: 44, 2: 44, 4: 48, 1: 31})
[datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18), d

In [ ]:
#for 1st April
print(RPS_10m.iloc[18].mean())
#for 29 April 
print(RPS_10m.iloc[37].mean())
#for 27 May
print(RPS_10m.iloc[57].mean())
RPS_10m.mean(axis=1)

0.1613998163452709
0.16057906336088154
0.16324058769513314


date
2022-03-07    0.159572
2022-03-08    0.161801
2022-03-09    0.155562
2022-03-10    0.158334
2022-03-11    0.157149
2022-03-14    0.159862
2022-03-15    0.161223
2022-03-16    0.156589
2022-03-17    0.159067
2022-03-18    0.155793
2022-03-21    0.159930
2022-03-22    0.154563
2022-03-23    0.160816
2022-03-24    0.154774
2022-03-25    0.161762
2022-03-28    0.162239
2022-03-29    0.153695
2022-03-30    0.160918
2022-03-31    0.161400
2022-04-01    0.162765
2022-04-04    0.153334
2022-04-05    0.155308
2022-04-06    0.155062
2022-04-07    0.153878
2022-04-08    0.166351
2022-04-11    0.155056
2022-04-12    0.162911
2022-04-13    0.153774
2022-04-14    0.155594
2022-04-18    0.165149
2022-04-19    0.157980
2022-04-20    0.156668
2022-04-21    0.160729
2022-04-22    0.160044
2022-04-25    0.153662
2022-04-26    0.155698
2022-04-27    0.159301
2022-04-28    0.160579
2022-04-29    0.164600
2022-05-02    0.154590
2022-05-03    0.160610
2022-05-04    0.151526
2022-05-05    0.150214
2022-0

#####One year (253)
***

In [ ]:
t_1y=pred(rd3,3)
t_1y=pd.DataFrame.from_dict(t_1y)
t_1y.set_index('date')
RPS_1y= RPS_data(t_1y,rd)
RPS_1y= create_RPS(t_1y,RPS_1y)
RPS_1y
print(RPS_1y.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
Name: ROST, dtype: int64 mikos 253
5 defaultdict(<class 'int'>, {4: 53, 3: 37, 1: 65, 5: 50, 2: 48})
[datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18), datetime.date(2022, 3, 21), datetime.date(2022, 3, 22), datetime.date(2022, 3, 23), datetime.date(2022, 3, 24), datetime.date(2022, 3, 25), datetime.date(2022, 3, 28), datetime.date(2022, 3, 29), datetime.date(2022, 3, 30), datetime.date(2022, 3, 31), datetime.date(2022, 4, 1), datetime.date(2022, 4, 4), datetime.date(2022, 4, 5), datetime.date(2022, 4, 6), datetime.date(2022, 4, 7), datetime.date(2022, 4, 8), datetime.date(2022, 4, 11), datetime.date(2022, 4, 12), datetime.date(2022, 4, 13)]
arxi Date
2021-04-14    4
Name: ROST, dtype: int64 kai telos  Date
2

In [ ]:
#for 1st April
print(RPS_1y.iloc[18].mean())
#for 29 April 
print(RPS_1y.iloc[37].mean())
#for 27 May
print(RPS_1y.iloc[57].mean())
RPS_1y.mean(axis=1)

0.16166795988758526
0.16054589545567374
0.16076989173397493


date
2022-03-07    0.160196
2022-03-08    0.161220
2022-03-09    0.156116
2022-03-10    0.158178
2022-03-11    0.156604
2022-03-14    0.159281
2022-03-15    0.160273
2022-03-16    0.157140
2022-03-17    0.159128
2022-03-18    0.156463
2022-03-21    0.159080
2022-03-22    0.156131
2022-03-23    0.160460
2022-03-24    0.155162
2022-03-25    0.161743
2022-03-28    0.161550
2022-03-29    0.154963
2022-03-30    0.160264
2022-03-31    0.161668
2022-04-01    0.162580
2022-04-04    0.153231
2022-04-05    0.154903
2022-04-06    0.156124
2022-04-07    0.153763
2022-04-08    0.163876
2022-04-11    0.155449
2022-04-12    0.162247
2022-04-13    0.154285
2022-04-14    0.155287
2022-04-18    0.163960
2022-04-19    0.157820
2022-04-20    0.157402
2022-04-21    0.161440
2022-04-22    0.159663
2022-04-25    0.153560
2022-04-26    0.155833
2022-04-27    0.158805
2022-04-28    0.160546
2022-04-29    0.163314
2022-05-02    0.154505
2022-05-03    0.160509
2022-05-04    0.153227
2022-05-05    0.152476
2022-0

#####All the samples (add each day another rank)
***

In [ ]:
#Αυτή η συνάρτηση παίρνει τα data και κάνει τη dummy μέτρηση για το διάστημα ενός χρόνου (όσο οριστεί στην ουσία το insample) για μια μετοχή
n=dict() 
def dummy2(st,i):
  flag=False
  insample=st.iloc[:-i]
  print('arxi',insample.head(1),'kai telos ',insample.tail(1),'mikos',len(insample))
  # if(len(insample)!=253):
  #   print('---------------------------------------------------------------',flag)
  count=defaultdict(int)
  for word in insample.values:
    count[word]+=1
  print(word,count)
  count=sorted(count.items()) #list Η πρώτη τιμή είναι η κλάση και η δεύτερη πόσες φορές είδα τον αριθμό.
  temp=[]
  for k in range(5):
    flag=True
    for l in count:
      if(l[0]==k+1):
        temp.append(l[1]/len(insample))
        flag=False
        break
    if(flag):
      temp.append(0)
  # print(temp,count)
  data={
      'prediction':temp
  }
  forecast=pd.DataFrame(data)
  return forecast
# #για όλες τις μετοχές υπολογίζεται το counter τους
dummy2(rd3['ABBV'],60)


arxi Date
2021-03-01    3
Name: ABBV, dtype: int64 kai telos  Date
2022-03-03    3
Name: ABBV, dtype: int64 mikos 256
3 defaultdict(<class 'int'>, {3: 55, 2: 50, 1: 38, 4: 56, 5: 57})


prediction
0    0.148438
1    0.195312
2    0.214844
3    0.218750
4    0.222656

In [ ]:
def pred2(st):
  pred=dict()
  for j in st:
    temp=[]
    date=[]
    for i in range(59,1,-1):
      # print(i)
      date.append(rd3[j].iloc[-i:-i+1].index.date[0])
      print(date)
      temp.append(dummy2(rd3[j],i)['prediction'].values)
      # pred[rd3[j].name]=temp
    #for the last day 
    date.append(rd3[j].iloc[-1:].index.date[0])
    temp.append(dummy2(rd3[j],1)['prediction'].values)
    pred[rd3[j].name]=temp
  # print(date)
  pred['date']=date
  pred_final=pd.DataFrame.from_dict(pred)
  # pred_final['Date']=date
  # pred_final.set_index('Date')
  # print(pred_final)
  return pred_final


In [ ]:
t_all=pred2(rd3)
t_all=pd.DataFrame.from_dict(t_all)
t_all.set_index('date')
RPS_all= RPS_data(t_all,rd)
RPS_all= create_RPS(t_all,RPS_all)
RPS_all
print(RPS_all.mean(axis=1).mean())

Η έξοδος ροής περικόπηκε στις τελευταίες 5000 γραμμές.
Name: ROST, dtype: int64 mikos 283
5 defaultdict(<class 'int'>, {1: 74, 5: 58, 2: 53, 4: 56, 3: 42})
[datetime.date(2022, 3, 7), datetime.date(2022, 3, 8), datetime.date(2022, 3, 9), datetime.date(2022, 3, 10), datetime.date(2022, 3, 11), datetime.date(2022, 3, 14), datetime.date(2022, 3, 15), datetime.date(2022, 3, 16), datetime.date(2022, 3, 17), datetime.date(2022, 3, 18), datetime.date(2022, 3, 21), datetime.date(2022, 3, 22), datetime.date(2022, 3, 23), datetime.date(2022, 3, 24), datetime.date(2022, 3, 25), datetime.date(2022, 3, 28), datetime.date(2022, 3, 29), datetime.date(2022, 3, 30), datetime.date(2022, 3, 31), datetime.date(2022, 4, 1), datetime.date(2022, 4, 4), datetime.date(2022, 4, 5), datetime.date(2022, 4, 6), datetime.date(2022, 4, 7), datetime.date(2022, 4, 8), datetime.date(2022, 4, 11), datetime.date(2022, 4, 12), datetime.date(2022, 4, 13)]
arxi Date
2021-03-01    1
Name: ROST, dtype: int64 kai telos  Date
2

In [ ]:
#for 1st April
print(RPS_all.iloc[18].mean())
#for 29 April 
print(RPS_all.iloc[37].mean())
#for 27 May
print(RPS_all.iloc[57].mean())
RPS_all.mean(axis=1)

0.1613432359963269
0.16045063528056724
0.15877569971285738


date
2022-03-07    0.159914
2022-03-08    0.161433
2022-03-09    0.155727
2022-03-10    0.158053
2022-03-11    0.156538
2022-03-14    0.159891
2022-03-15    0.160638
2022-03-16    0.157908
2022-03-17    0.159570
2022-03-18    0.155599
2022-03-21    0.158897
2022-03-22    0.155690
2022-03-23    0.160747
2022-03-24    0.155114
2022-03-25    0.162204
2022-03-28    0.161896
2022-03-29    0.154460
2022-03-30    0.160537
2022-03-31    0.161343
2022-04-01    0.162914
2022-04-04    0.153749
2022-04-05    0.155651
2022-04-06    0.156895
2022-04-07    0.153808
2022-04-08    0.162584
2022-04-11    0.156012
2022-04-12    0.161884
2022-04-13    0.154424
2022-04-14    0.155993
2022-04-18    0.163420
2022-04-19    0.156832
2022-04-20    0.157350
2022-04-21    0.161184
2022-04-22    0.159093
2022-04-25    0.153878
2022-04-26    0.156083
2022-04-27    0.159904
2022-04-28    0.160451
2022-04-29    0.162257
2022-05-02    0.155547
2022-05-03    0.161236
2022-05-04    0.153295
2022-05-05    0.153579
2022-0

In [ ]:
#save the best results
RPS_1y.to_excel('Q1-dummy_1y.xlsx')